In [3]:
import pandas as pd

In [4]:

df = pd.read_csv("/Users/andre/Downloads/UNIUSDT-trades-2024-11.csv",
                names = ["id","price","qty","quote_qty","time","is_buyer_maker","is_best_match"])

df.time = pd.to_datetime(df.time, unit="ms")
df.set_index("time", inplace = True)
df

id   price    qty  quote_qty  is_buyer_maker  \
time                                                                           
2024-11-01 00:00:01.827  160987021   7.614   0.66    5.02524           False   
2024-11-01 00:00:01.827  160987022   7.614   0.32    2.43648           False   
2024-11-01 00:00:02.047  160987023   7.614   0.45    3.42630           False   
2024-11-01 00:00:02.047  160987024   7.615   2.16   16.44840           False   
2024-11-01 00:00:02.053  160987025   7.614  16.11  122.66154            True   
...                            ...     ...    ...        ...             ...   
2024-11-30 23:59:54.605  168671298  12.782  25.88  330.79816           False   
2024-11-30 23:59:54.605  168671299  12.782  24.12  308.30184           False   
2024-11-30 23:59:57.557  168671300  12.782  50.00  639.10000           False   
2024-11-30 23:59:59.113  168671301  12.782  36.00  460.15200            True   
2024-11-30 23:59:59.113  168671302  12.782  15.62  199.65484            True   

                         is_best_match  
time                                    
2024-11-01 00:00:01.827           True  
2024-11-01 00:00:01.827           True  
2024-11-01 00:00:02.047           True  
2024-11-01 00:00:02.047           True  
2024-11-01 00:00:02.053           True  
...                                ...  
2024-11-30 23:59:54.605           True  
2024-11-30 23:59:54.605           True  
2024-11-30 23:59:57.557           True  
2024-11-30 23:59:59.113           True  
2024-11-30 23:59:59.113           True  

[7684282 rows x 6 columns]

In [6]:
df["buy_vol"] = df.qty * (1 - df["is_buyer_maker"])
df["sell_vol"] = df.qty * df["is_buyer_maker"]
df["vol_delta"] = df["buy_vol"] - df["sell_vol"]

df

id   price    qty  quote_qty  is_buyer_maker  \
time                                                                           
2024-11-01 00:00:01.827  160987021   7.614   0.66    5.02524           False   
2024-11-01 00:00:01.827  160987022   7.614   0.32    2.43648           False   
2024-11-01 00:00:02.047  160987023   7.614   0.45    3.42630           False   
2024-11-01 00:00:02.047  160987024   7.615   2.16   16.44840           False   
2024-11-01 00:00:02.053  160987025   7.614  16.11  122.66154            True   
...                            ...     ...    ...        ...             ...   
2024-11-30 23:59:54.605  168671298  12.782  25.88  330.79816           False   
2024-11-30 23:59:54.605  168671299  12.782  24.12  308.30184           False   
2024-11-30 23:59:57.557  168671300  12.782  50.00  639.10000           False   
2024-11-30 23:59:59.113  168671301  12.782  36.00  460.15200            True   
2024-11-30 23:59:59.113  168671302  12.782  15.62  199.65484            True   

                         is_best_match  buy_vol  sell_vol  vol_delta  
time                                                                  
2024-11-01 00:00:01.827           True     0.66      0.00       0.66  
2024-11-01 00:00:01.827           True     0.32      0.00       0.32  
2024-11-01 00:00:02.047           True     0.45      0.00       0.45  
2024-11-01 00:00:02.047           True     2.16      0.00       2.16  
2024-11-01 00:00:02.053           True     0.00     16.11     -16.11  
...                                ...      ...       ...        ...  
2024-11-30 23:59:54.605           True    25.88      0.00      25.88  
2024-11-30 23:59:54.605           True    24.12      0.00      24.12  
2024-11-30 23:59:57.557           True    50.00      0.00      50.00  
2024-11-30 23:59:59.113           True     0.00     36.00     -36.00  
2024-11-30 23:59:59.113           True     0.00     15.62     -15.62  

[7684282 rows x 9 columns]

In [7]:
vol_delta = df["vol_delta"]
vol_delta

time
2024-11-01 00:00:01.827     0.66
2024-11-01 00:00:01.827     0.32
2024-11-01 00:00:02.047     0.45
2024-11-01 00:00:02.047     2.16
2024-11-01 00:00:02.053   -16.11
                           ...  
2024-11-30 23:59:54.605    25.88
2024-11-30 23:59:54.605    24.12
2024-11-30 23:59:57.557    50.00
2024-11-30 23:59:59.113   -36.00
2024-11-30 23:59:59.113   -15.62
Name: vol_delta, Length: 7684282, dtype: float64

In [8]:

cvd = vol_delta.groupby(pd.Grouper(freq="7D")).cumsum()
cvd

time
2024-11-01 00:00:01.827        0.66
2024-11-01 00:00:01.827        0.98
2024-11-01 00:00:02.047        1.43
2024-11-01 00:00:02.047        3.59
2024-11-01 00:00:02.053      -12.52
                             ...   
2024-11-30 23:59:54.605   -94748.47
2024-11-30 23:59:54.605   -94724.35
2024-11-30 23:59:57.557   -94674.35
2024-11-30 23:59:59.113   -94710.35
2024-11-30 23:59:59.113   -94725.97
Name: vol_delta, Length: 7684282, dtype: float64

In [9]:
cvd_candles = cvd.resample("1H").agg(["max","min","first","last"])
cvd_candles.columns = ["high","low","open","close"]
cvd_candles

/var/folders/33/gyg8_bbj4qn5_tvszhbzjxdm0000gn/T/ipykernel_23576/1139652399.py:1: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  cvd_candles = cvd.resample("1H").agg(["max","min","first","last"])


high        low       open      close
time                                                          
2024-11-01 00:00:00  15813.97    -253.70       0.66   10898.95
2024-11-01 01:00:00  22052.74    4458.03   10900.58    8259.17
2024-11-01 02:00:00  28625.21     198.98    8304.68   13461.22
2024-11-01 03:00:00  31253.31   -7550.49   13658.84   -5613.35
2024-11-01 04:00:00  -2345.99   -7370.97   -5611.92   -5888.56
...                       ...        ...        ...        ...
2024-11-30 19:00:00 -87394.35 -101358.40  -88004.20  -89159.23
2024-11-30 20:00:00 -88491.20 -107917.57  -89130.20  -92643.05
2024-11-30 21:00:00 -92635.85 -104176.48  -92644.61 -100079.66
2024-11-30 22:00:00 -86592.81 -103639.63 -100101.54  -86806.51
2024-11-30 23:00:00 -82665.73  -99687.23  -86803.14  -94725.97

[720 rows x 4 columns]

In [10]:
import plotly.graph_objects as go

fig = go.Figure(data=[go.Candlestick(
            x = cvd_candles.index,
            open = cvd_candles.open,
            high = cvd_candles.high,
            low = cvd_candles.low,
            close = cvd_candles.close)])

fig.update_layout(xaxis_rangeslider_visible=False)

fig.show()



In [17]:
price_candles = df.price.resample("1min").agg(["max","min","first","last"])
price_candles.columns = ["high","low","open","close"]
price_candles

high     low    open   close
time                                               
2024-11-01 00:00:00   7.624   7.613   7.614   7.619
2024-11-01 00:01:00   7.639   7.617   7.617   7.639
2024-11-01 00:02:00   7.641   7.630   7.638   7.633
2024-11-01 00:03:00   7.648   7.636   7.642   7.647
2024-11-01 00:04:00   7.659   7.645   7.647   7.655
...                     ...     ...     ...     ...
2024-11-30 23:55:00  12.797  12.785  12.792  12.791
2024-11-30 23:56:00  12.796  12.776  12.791  12.776
2024-11-30 23:57:00  12.787  12.762  12.777  12.773
2024-11-30 23:58:00  12.795  12.773  12.773  12.795
2024-11-30 23:59:00  12.795  12.781  12.793  12.782

[43200 rows x 4 columns]

In [18]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = make_subplots(rows=2, cols=1, shared_xaxes=True)

fig = fig.add_trace(go.Candlestick(
            x = price_candles.index,
            open = price_candles.open,
            high = price_candles.high,
            low = price_candles.low,
            close = price_candles.close),
        row=1, col=1)

fig = fig.add_trace(go.Candlestick(
            x = cvd_candles.index,
            open = cvd_candles.open,
            high = cvd_candles.high,
            low = cvd_candles.low,
            close = cvd_candles.close),
        row=2, col=1)

fig.update_xaxes(rangeslider_visible=False)

fig.show()